In [ ]:
# ..... get pseudobulk matrices across stages ..... #

In [ ]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)

In [3]:
# get pseudo-bulk for CPM data
get_cpm_pseudo_bulk <- function(scdata, ctype_list){      
        
    new_labels = scdata$ctypes
    nbds = unique(new_labels)
    nbds <- nbds[which(!is.na(nbds) & nbds!='unassigned')]
    sc_sub2 = matrix(NA, nrow = dim(scdata)[1], ncol = length(nbds))
    
    for (i in 1:length(nbds)){
        cols = which(new_labels==nbds[i])
    
        if(length(cols)>1){
            sc_sub2[,i] = rowSums(cpm(scdata)[,cols])/length(cols)
        }else if(length(cols)==1){            
            sc_sub2[,i] = cpm(scdata)[,cols]
        }else{
            sc_sub2[,i] = NA
        }
    }    
    rownames(sc_sub2) = rownames(scdata)
    colnames(sc_sub2) = nbds
    return(sc_sub2[,ctype_list])
}

In [16]:
# cell type order
# ctype_order = c('vCM', 'aCM', 'immature-CM', 'endothelial', 'endocardial', 'epicardial',
                # 'fibroblast', 'SMC', 'pericyte', 'neural-crest', 'blood', 'macrophage')

ctype_order = c('LV_vCM', 'RV_vCM', 'aCM', 'immature_CM', 'endocardial', 'epicardial',
                'mes_progenitor', 'fibroblast', 'SMC', 'neural_crest', 'blood', 'macrophage')
length(ctype_order)

[1] 12

In [22]:
# load integrated data
sc1 = readRDS('lizard_integrated_ssSTACAS.rds')
DefaultAssay(sc1) <- 'RNA'

# get harmonised labels
tab1 = read.delim('lizard_ssSTACAS_celltypes.txt', sep = '\t')
tab1[1,]

sc1$stage = sc1$orig.ident
sc1$broad_type = tab1$subtype[match(sc1$seurat_clusters, tab1$cluster)]
sc1$cluster = tab1$label[match(sc1$seurat_clusters, tab1$cluster)]
sc1$ctypes <- sc1$cluster  # sub('\\_.*', '', sc1$cluster)
sc1@meta.data[1,]

species cluster celltype subtype label cluster_new
1 lizard  0       Myeloid  blood   blood c1

orig.ident nCount_RNA nFeature_RNA species
stage9_sample1_AAACCCAAGACCATGG-1 stage9     3853       1832         lizard 
                                  dataset        consensus_type
stage9_sample1_AAACCCAAGACCATGG-1 stage9_sample1 NA            
                                  integrated_snn_res.1 seurat_clusters stage 
stage9_sample1_AAACCCAAGACCATGG-1 9                    9               stage9
                                  broad_type  cluster     ctypes     
stage9_sample1_AAACCCAAGACCATGG-1 endocardial endocardial endocardial

In [23]:
# make SCE object
sce2 = SingleCellExperiment(list(counts = sc1@assays$RNA@counts), colData = DataFrame(sc1@meta.data))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))
sce2

class: SingleCellExperiment 
dim: 22732 75708 
metadata(0):
assays(2): counts cpm
rownames(22732): LOC132761864 LOC132781240 ... MT-nad6 MT-cob
rowData names(0):
colnames(75708): stage9_sample1_AAACCCAAGACCATGG-1
  stage9_sample1_AAACCCAAGTAACGAT-1 ...
  stage16_sample3_TTTGTTGGTTCCTACC-1 stage16_sample3_TTTGTTGTCAGTGTTG-1
colData names(12): orig.ident nCount_RNA ... cluster ctypes
reducedDimNames(0):
mainExpName: NULL
altExpNames(0):

In [24]:
# create pseudo-bulk matrices for all genes
scbulk1 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage9'], ctype_order)
scbulk2 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage13'], ctype_order)
scbulk3 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage16'], ctype_order)

scbulk1[c('TBX5','COL3A1'),]

LV_vCM    RV_vCM    aCM       immature_CM endocardial epicardial
TBX5   359.45333 346.73075 671.70557 118.67783    34.00338    52.84446 
COL3A1  17.97906  16.26408  20.01893  67.32364   697.43645   492.12037 
       mes_progenitor fibroblast SMC      neural_crest blood     macrophage
TBX5    21.82208       86.95897  325.2235  8.515131     3.757648 11.62961  
COL3A1 114.68799      333.56914  184.5743 84.575834    18.045733 90.42143

In [25]:
# save
save(scbulk1, scbulk2, scbulk3, file = 'lizard_integrated_pseudobulk_expression_matrices.Rdata')

In [26]:
colnames(scbulk1) <- paste0('s1|', colnames(scbulk1))
colnames(scbulk2) <- paste0('s2|', colnames(scbulk2))
colnames(scbulk3) <- paste0('s3|', colnames(scbulk3))

dfnew = cbind(scbulk1, scbulk2, scbulk3)

# save
save(dfnew, file = 'lizard_full_integrated_pseudobulk_expression_matrix.Rdata')